In [1]:
from dnd.monsters.circus_fighter import create_warrior
from dnd.entity import Entity
from dnd.blocks.equipment import WeaponSlot
from dnd.core.dice import Dice, RollType, AttackOutcome
from uuid import uuid4
from dnd.core.events import EventQueue

import time
from uuid import UUID



In [2]:
start_time = time.time()
source_id = uuid4()
proficiency_bonus = 2

In [3]:
q = EventQueue()

In [4]:
warrior = create_warrior(source_id,proficiency_bonus,position=(0,0))
# q._all_events


In [5]:
warrior2 = create_warrior(name="Mona",position=(1,1))
# q._all_events


In [6]:
from dnd.core.events import Event, EventType, EventPhase
from typing import Optional
from dnd.core.base_tiles import floor_factory

In [7]:
flor_00 = floor_factory((0,0))
flor_01 = floor_factory((0,1))
flor_10 = floor_factory((1,0))
flor_11 = floor_factory((1,1))


In [8]:
from dnd.actions import Attack, AttackEvent, Movement, MovementEvent
weapon_slot = WeaponSlot.MAIN_HAND

In [9]:
Entity.update_all_entities_senses()


paths before filtering: {(0, 0): [(0, 0)], (0, 1): [(0, 0), (0, 1)], (1, 0): [(0, 0), (1, 0)], (1, 1): [(0, 0), (1, 1)]}
paths before filtering: {(1, 1): [(1, 1)], (1, 0): [(1, 1), (1, 0)], (0, 1): [(1, 1), (0, 1)], (0, 0): [(1, 1), (0, 0)]}


In [10]:
attack = Attack(name="Warrior Main Hand attack",
                source_entity_uuid=warrior.uuid,
                target_entity_uuid=warrior2.uuid,
                weapon_slot= WeaponSlot.MAIN_HAND)
                
attack2=Attack(name="Warrior2 Main Hand attack",
               source_entity_uuid=warrior2.uuid,
               target_entity_uuid=warrior.uuid,
               weapon_slot= WeaponSlot.MAIN_HAND)


In [11]:
Entity.update_all_entities_senses()

print(warrior.senses.paths)

paths before filtering: {(0, 0): [(0, 0)], (0, 1): [(0, 0), (0, 1)], (1, 0): [(0, 0), (1, 0)], (1, 1): [(0, 0), (1, 1)]}
paths before filtering: {(1, 1): [(1, 1)], (1, 0): [(1, 1), (1, 0)], (0, 1): [(1, 1), (0, 1)], (0, 0): [(1, 1), (0, 0)]}
defaultdict(<class 'list'>, {(0, 0): [(0, 0)], (0, 1): [(0, 0), (0, 1)], (1, 0): [(0, 0), (1, 0)], (1, 1): [(0, 0), (1, 1)]})


In [12]:
movement = Movement(name="Warrior Movement",
                    source_entity_uuid=warrior.uuid,
                    end_position=(1,1))


In [13]:
movement.costs

[Cost(name='Movement Cost', cost_type='movement', cost=2, evaluator=<function entity_action_economy_cost_evaluator at 0x0000026186DEC680>)]

In [14]:
movement.check_costs()

True

In [15]:
print(warrior.position)
movement.apply()


(0, 0)
paths before filtering: {(1, 1): [(1, 1)], (1, 0): [(1, 1), (1, 0)], (0, 1): [(1, 1), (0, 1)], (0, 0): [(1, 1), (0, 0)]}
paths before filtering: {(1, 1): [(1, 1)], (1, 0): [(1, 1), (1, 0)], (0, 1): [(1, 1), (0, 1)], (0, 0): [(1, 1), (0, 0)]}


MovementEvent(name='Warrior Movement', uuid=UUID('d545cc1b-5fb5-4855-9be9-615db1649399'), source_entity_uuid=UUID('dede6495-c257-4f02-9036-c893cd158a9a'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, lineage_uuid=UUID('ec437bdc-c45f-4bd3-8a53-eaee1bbd2f22'), timestamp=datetime.datetime(2025, 5, 17, 17, 16, 44, 656136), event_type=<EventType.MOVEMENT: 'movement'>, phase=<EventPhase.COMPLETION: 'completion'>, modified=True, canceled=False, parent_event=None, status_message='Applied movement for Warrior Movement', lineage_children_events=[], children_events=[], costs=[Cost(name='Movement Cost', cost_type='movement', cost=2, evaluator=<function entity_action_economy_cost_evaluator at 0x0000026186DEC680>)], start_position=(0, 0), end_position=(1, 1), path=[(0, 0), (1, 1)])

In [17]:
print(warrior.position)


(1, 1)


In [10]:
from dnd.core.events import Trigger, EventHandler, EventProcessor

In [11]:
attack_trigger = Trigger(name="Attack Trigger",
                         event_type=EventType.ATTACK,
                         event_phase=EventPhase.DECLARATION)



def attack_processor(event: AttackEvent, source_entity_uuid: UUID ) -> Optional[AttackEvent]:
    print(f"Simple Attack event received for {source_entity_uuid} with target {event.target_entity_uuid} in phase {event.phase}")
    return event

def precise_attack_processor(event: AttackEvent, source_entity_uuid: UUID ) -> Optional[AttackEvent]:
    print(f"Precise attack event received for {source_entity_uuid} with target {event.target_entity_uuid} in phase {event.phase}")
    return event

test_handler = EventHandler(name="Test Handler",
                            trigger_conditions=[attack_trigger],
                            event_processor=attack_processor,
                            source_entity_uuid=warrior2.uuid)



precise_attack_trigger = Trigger(name="Attack Trigger",
                         event_type=EventType.ATTACK,
                         event_phase=EventPhase.DECLARATION,
                         event_source_entity_uuid=warrior.uuid,
                         event_target_entity_uuid=warrior2.uuid)
test_precise_handler = EventHandler(name="Test Precise Handler",
                                    trigger_conditions=[precise_attack_trigger],
                                    event_processor=precise_attack_processor,
                                    source_entity_uuid=warrior2.uuid)



In [12]:
test_handler.trigger_conditions[0].is_simple()

True

In [13]:
warrior2.add_event_handler(test_handler)
warrior2.add_event_handler(test_precise_handler)

In [14]:
warrior2.get_hp()

58

In [15]:
# Trigger condition: event_type=<EventType.ATTACK: 'attack'> event_phase=<EventPhase.DECLARATION: 'declaration'> event_source_entity_uuid=UUID('7f40519e-37ae-411d-81e9-90fafbccdd92') event_target_entity_uuid=UUID('9ec24cff-1dc5-4af7-a768-db9962dea6ea')


In [16]:
#measure time of attack
start_time = time.time()
attack.apply()
attack_time = time.time()-start_time
print(f"Attack time: {attack_time}")

Simple Attack event received for 215b422b-e88f-4efe-a71f-f330d7fbec39 with target 215b422b-e88f-4efe-a71f-f330d7fbec39 in phase EventPhase.DECLARATION
Precise attack event received for 215b422b-e88f-4efe-a71f-f330d7fbec39 with target 215b422b-e88f-4efe-a71f-f330d7fbec39 in phase EventPhase.DECLARATION
Simple Attack event received for 215b422b-e88f-4efe-a71f-f330d7fbec39 with target 215b422b-e88f-4efe-a71f-f330d7fbec39 in phase EventPhase.DECLARATION
Precise attack event received for 215b422b-e88f-4efe-a71f-f330d7fbec39 with target 215b422b-e88f-4efe-a71f-f330d7fbec39 in phase EventPhase.DECLARATION
Simple Attack event received for 215b422b-e88f-4efe-a71f-f330d7fbec39 with target 215b422b-e88f-4efe-a71f-f330d7fbec39 in phase EventPhase.DECLARATION
Precise attack event received for 215b422b-e88f-4efe-a71f-f330d7fbec39 with target 215b422b-e88f-4efe-a71f-f330d7fbec39 in phase EventPhase.DECLARATION
Attack time: 0.004500389099121094


In [17]:
warrior2.remove_event_handler(test_handler)

In [18]:
attack2.apply()

AttackEvent(name='Warrior2 Main Hand attack', uuid=UUID('bd727639-6ef2-471a-abca-3b5842518368'), source_entity_uuid=UUID('215b422b-e88f-4efe-a71f-f330d7fbec39'), source_entity_name=None, target_entity_uuid=UUID('07e1eef9-bf2a-4975-825a-cb317e6ed4e6'), target_entity_name=None, context=None, lineage_uuid=UUID('6cc6e7db-dbc3-4564-954c-dcd1deda2844'), timestamp=datetime.datetime(2025, 5, 17, 12, 1, 31, 937515), event_type=<EventType.ATTACK: 'attack'>, phase=<EventPhase.COMPLETION: 'completion'>, modified=True, canceled=False, parent_event=None, status_message='Attack completed', lineage_children_events=[], children_events=[], costs=[Cost(name='Attack Cost', cost_type='actions', cost=1, evaluator=<function entity_action_economy_cost_evaluator at 0x000001B787C5A020>)], weapon_slot=<WeaponSlot.MAIN_HAND: 'MAIN_HAND'>, range=Range(type=<RangeType.REACH: 'Reach'>, normal=5, long=None), attack_bonus=ModifiableValue(name='Value_Attack Bonus_Attack Bonus_Melee Attack Bonus_strength Ability Score_s

In [19]:
warrior.get_damages(weapon_slot=WeaponSlot.MAIN_HAND,target_entity_uuid=warrior.uuid)

[Damage(name='Damage', uuid=UUID('75c7c6d6-b15d-4414-8119-587fd2f5f00f'), source_entity_uuid=UUID('07e1eef9-bf2a-4975-825a-cb317e6ed4e6'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, damage_dice=6, dice_numbers=1, damage_bonus=ModifiableValue(name='Damage Bonus_strength Ability Score_strength Modifier Bonus_Melee Damage Bonus_Damage Bonus', uuid=UUID('4769838a-2f00-48c3-829f-7be5e7b17dd6'), source_entity_uuid=UUID('07e1eef9-bf2a-4975-825a-cb317e6ed4e6'), source_entity_name=None, target_entity_uuid=UUID('07e1eef9-bf2a-4975-825a-cb317e6ed4e6'), target_entity_name=None, context=None, score_normalizer=<function ModifiableValue.create.<locals>.<lambda> at 0x000001B787E6CC20>, generated_from=[UUID('5e2ca655-a9d3-43c3-a022-a9e60b5184dc'), UUID('11d7cca2-bdf8-4c35-855a-35a2c7783863'), UUID('38de5b96-43eb-4882-9ccb-a504225f44f6'), UUID('5e2ca655-a9d3-43c3-a022-a9e60b5184dc')], global_normalizer=False, self_static=StaticValue(name='A Value_A Value_A V

In [12]:
for event in q._all_events:
    print(event.name,event.status_message)


Performer's Leather Armor None
Performer's Leather Armor None
Performer's Leather Armor None
Performer's Leather Armor None
Flaming Scimitar None
Flaming Scimitar None
Flaming Scimitar None
Flaming Scimitar None
Rusty Dagger None
Rusty Dagger None
Rusty Dagger None
Rusty Dagger None
Dual Wielder None
Dual Wielder Applied Dual Wielder contextual ac modifer condition to Ganger
Dual Wielder Applied Dual Wielder contextual ac modifer condition to Ganger
Elemental Weapon Mastery None
Elemental Weapon Mastery Applied Elemental Weapon Mastery contextual advantage modifier condition to Ganger
Elemental Weapon Mastery Applied Elemental Weapon Mastery contextual advantage modifier condition to Ganger
Elemental Affinity None
Elemental Affinity Applied Elemental Affinity resistance modifier condition to Ganger
Elemental Affinity Applied Elemental Affinity resistance modifier condition to Ganger
Circus Performer None
Circus Performer Applied Circus Performer condition to Ganger
Circus Performer App

In [13]:
warrior2.get_hp()

54

In [14]:
warrior.action_economy.actions.normalized_score

0

In [15]:
warrior.action_economy.actions.self_static.value_modifiers

{UUID('ae6a0176-d3df-4528-bcfd-d5ccf8c469e8'): NumericalModifier(name='Actions_base_value', uuid=UUID('ae6a0176-d3df-4528-bcfd-d5ccf8c469e8'), source_entity_uuid=UUID('af7d2079-0a4a-4228-8cc7-18554f5f86aa'), source_entity_name=None, target_entity_uuid=UUID('af7d2079-0a4a-4228-8cc7-18554f5f86aa'), target_entity_name=None, context=None, value=1, score_normalizer=<function ModifiableValue.create.<locals>.<lambda> at 0x00000182A63300E0>, normalized_value=1),
 UUID('07800008-c663-4e07-91fc-4b6af1bdc040'): NumericalModifier(name='cost', uuid=UUID('07800008-c663-4e07-91fc-4b6af1bdc040'), source_entity_uuid=UUID('af7d2079-0a4a-4228-8cc7-18554f5f86aa'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, value=-1, score_normalizer=None, normalized_value=-1)}

In [ ]:
warrior.action_economy.reset_all_costs()

In [17]:
warrior.action_economy.actions.normalized_score

1

In [14]:
warrior.source_entity_uuid

UUID('26ced8d6-9c02-4212-9670-1e5bbb096e83')

In [15]:
warrior.ability_scores.uuid


UUID('4bf62a8d-f496-44e9-b0ed-ddb80abd6d21')

In [16]:
Entity.get(warrior.source_entity_uuid)

Entity(name='Ganger', description='A level 4 fighter character with a past in the circus and spiked claws for hands.', uuid=UUID('26ced8d6-9c02-4212-9670-1e5bbb096e83'), source_entity_uuid=UUID('26ced8d6-9c02-4212-9670-1e5bbb096e83'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, blocks={UUID('4bf62a8d-f496-44e9-b0ed-ddb80abd6d21'): AbilityScores(name='ability_scores', description=None, uuid=UUID('4bf62a8d-f496-44e9-b0ed-ddb80abd6d21'), source_entity_uuid=UUID('26ced8d6-9c02-4212-9670-1e5bbb096e83'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, blocks={UUID('231cdc5b-de31-4f75-abae-dfd42987107f'): Ability(name='strength', description=None, uuid=UUID('231cdc5b-de31-4f75-abae-dfd42987107f'), source_entity_uuid=UUID('26ced8d6-9c02-4212-9670-1e5bbb096e83'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, blocks={}, values={UUID('4acab144-14a4-44ce-9897-1e8de35c602

In [17]:
from dnd.conditions import Paralyzed

In [18]:
paralyzed_condition = Paralyzed(source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid)
paralyzed_condition.apply()


ConditionApplicationEvent(name='Paralyzed', uuid=UUID('f786dab7-daa2-4c92-b3a5-799509eb8f03'), source_entity_uuid=UUID('26ced8d6-9c02-4212-9670-1e5bbb096e83'), source_entity_name=None, target_entity_uuid=UUID('72649558-23a3-4397-b5be-2abc1fa36c78'), target_entity_name=None, context=None, lineage_uuid=UUID('9b0e900e-a1c5-4cdf-95f2-ffacf0295769'), timestamp=datetime.datetime(2025, 5, 11, 19, 9, 3, 810441), event_type=<EventType.CONDITION_APPLICATION: 'condition_application'>, phase=<EventPhase.COMPLETION: 'completion'>, modified=True, canceled=False, parent_event=None, status_message='Applied Paralyzed to target contextual critical modifier to Mona', lineage_children_events=[UUID('a9b3031e-e6e3-420f-a7ba-3e8fea24e13a'), UUID('219eb697-cc94-4117-82f8-90bc5bc98c68'), UUID('f8796037-ca17-4349-8eae-2bd721c08d58'), UUID('b1e88ea5-b149-4477-b1c0-6af5c568fc38'), UUID('d2cedcd6-df90-4d8a-8a5a-4190a8f53fd3'), UUID('ffece060-7512-45f7-b464-d44834654be9'), UUID('a9b3031e-e6e3-420f-a7ba-3e8fea24e13a

In [ ]:
weapon_slot = WeaponSlot.MAIN_HAND

warrior_bonus = warrior.attack_bonus(target_entity_uuid=warrior2.source_entity_uuid,weapon_slot=weapon_slot)

In [ ]:
warrior.ability_scores.get_ability("strength").ability_score.normalized_score+warrior.ability_scores.get_ability("strength").modifier_bonus.normalized_score



In [ ]:
warrior_bonus.normalized_score

In [ ]:
attack_dice = Dice(count=1,value=20,bonus=warrior_bonus, roll_type=RollType.ATTACK)
attack_roll = attack_dice.roll
print(f"Attack roll result: {attack_roll.total}")








In [ ]:
attack_roll.bonus

In [ ]:
attack_roll.results

In [13]:
import time

In [ ]:
start_time = time.time()
damages = warrior.get_damages(weapon_slot)
print(time.time()-start_time)

In [ ]:
start_time = time.time()
attack_bonus = warrior.attack_bonus(weapon_slot= weapon_slot)
print(time.time()-start_time)


In [ ]:
start_time = time.time()
ac = warrior2.ac_bonus()
print(time.time()-start_time)
start_time = time.time()

In [ ]:
damages

In [ ]:
start_time = time.time()
warrior.set_target_entity(warrior2.uuid)
print(time.time()-start_time)

In [21]:
warrior.target_entity_uuid=warrior2.uuid

In [22]:
a = warrior.uuid

In [ ]:
start_time = time.time()
warrior2.target_entity_name="warrior.uuid"
print(time.time()-start_time)

In [ ]:
start_time = time.time()
warrior2.target_entity_uuid=warrior.uuid
print(time.time()-start_time)

In [ ]:
start_time = time.time()
warrior2.set_target_entity(warrior.uuid)
print(time.time()-start_time)

In [ ]:
start_time = time.time()
warrior2.set_target_entity(warrior.uuid)
print(time.time()-start_time)

In [ ]:
start_time = time.time()
warrior.attack(warrior2.uuid,weapon_slot)
print(time.time()-start_time)


In [28]:
warrior_strenght_modifer = warrior.ability_scores.get_ability("strength").get_combined_values()
warrior_ac = warrior.ac_bonus()

In [ ]:
acrobatics_skill_request = warrior.create_skill_check_request(warrior2.uuid, "acrobatics",warrior_ac.uuid)
perception_skill_request = warrior.create_skill_check_request(warrior2.uuid, "perception",warrior_ac.uuid)
strength_saving_throw_request = warrior.create_saving_throw_request(warrior2.uuid, "strength",warrior_ac.uuid)

In [ ]:
acrobatics_skill_request

In [ ]:
strength_saving_throw_request

In [ ]:
warrior2.skill_bonus(warrior.uuid,skill_name="acrobatics")

In [ ]:
warrior2.skill_check(acrobatics_skill_request)

In [ ]:
warrior2.skill_check(perception_skill_request)

In [ ]:
warrior2.saving_throw_bonus(warrior.uuid, "strength")

In [ ]:
warrior2.saving_throw(strength_saving_throw_request)


In [ ]:
from dnd.conditions import Blinded
from dnd.core.events import EventQueue


blinded = Blinded(source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid)
blinded.apply()



In [ ]:

warrior2.equipment.attack_bonus.advantage


In [ ]:
warrior.equipment.attack_bonus.advantage


In [ ]:
blinded.modifers_uuids

In [ ]:
warrior2.skill_check(perception_skill_request)

In [ ]:
blinded.remove()


In [ ]:
warrior2.skill_check(perception_skill_request)

In [ ]:
warrior2.equipment.attack_bonus.advantage


In [48]:
from dnd.core.modifiers import ContextualNumericalModifier, NumericalModifier, ContextAwareNumerical
from typing import Optional, Dict, Any
from uuid import UUID


In [49]:
from dnd.conditions import Charmed

charmed = Charmed(source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid)


In [ ]:
charmed.apply()


In [ ]:
deception_skill_request = warrior2.create_skill_check_request(warrior.uuid, "deception",15)

warrior.skill_check(deception_skill_request)





In [53]:
def hate_mona(source_entity_uuid: UUID, target_entity_uuid: Optional[UUID]=None, context: Optional[Dict[str, Any]]=None) -> NumericalModifier:
    """ function that cheks if the target name is Mona, in that case it gives a +5 modifier"""
    if target_entity_uuid is not None:
        target_entity = Entity.get(target_entity_uuid)
    else:
        target_entity = None
    if isinstance(target_entity, Entity) and target_entity.name == "Mona":
        return NumericalModifier(source_entity_uuid=source_entity_uuid, target_entity_uuid=target_entity_uuid, value=5)
    else:
        return NumericalModifier(source_entity_uuid=source_entity_uuid, target_entity_uuid=target_entity_uuid, value=0)

hate_mona_modifier = ContextualNumericalModifier(name="Hate Mona",source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid, callable=hate_mona)


In [ ]:
warrior.equipment.attack_bonus.self_contextual.add_value_modifier(hate_mona_modifier)


In [ ]:
warrior.set_target_entity(warrior2.uuid)
warrior.equipment.attack_bonus.normalized_score


In [ ]:
warrior.clear_target_entity()
warrior.equipment.attack_bonus.normalized_score


In [57]:
warrior.senses.entities[warrior2.uuid]=(1,0)

In [ ]:
from dnd.conditions import Frightened
frightened = Frightened(source_entity_uuid=warrior2.uuid, target_entity_uuid=warrior.uuid)
frightened.apply()






In [ ]:
warrior.action_economy.movement.normalized_score


In [ ]:
warrior.senses.entities = {}
warrior.action_economy.movement.normalized_score


In [ ]:
print(f"total_time: {time.time()-start_time}")